In [3]:
import numpy as np 
import pandas as pd 
from datetime import date

In [4]:
ratios = [0,0.236, 0.382, 0.5 , 0.618, 0.786,1,1.414,1.618]
fiblevels = np.array(ratios)

In [5]:
def RSI(series, period=14):
    delta = series.diff().dropna()
    ups = delta * 0
    downs = ups.copy()
    ups[delta > 0] = delta[delta > 0]
    downs[delta < 0] = -delta[delta < 0]
    ups[ups.index[period-1]] = np.mean( ups[:period] ) #first value is sum of avg gains
    ups = ups.drop(ups.index[:(period-1)])
    downs[downs.index[period-1]] = np.mean( downs[:period] ) #first value is sum of avg losses
    downs = downs.drop(downs.index[:(period-1)])
    rs = ups.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() / \
         downs.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() 
    return 100 - 100 / (1 + rs)


# calculating Stoch RSI (gives the same values as TradingView)
# https://www.tradingview.com/wiki/Stochastic_RSI_(STOCH_RSI) 
def STRSIA(series, period=14, smoothK=3, smoothD=3):
    # Calculate RSI 
    delta = series.diff().dropna()
    ups = delta * 0
    downs = ups.copy()
    ups[delta > 0] = delta[delta > 0]
    downs[delta < 0] = -delta[delta < 0]
    ups[ups.index[period-1]] = np.mean( ups[:period] ) #first value is sum of avg gains
    ups = ups.drop(ups.index[:(period-1)])
    downs[downs.index[period-1]] = np.mean( downs[:period] ) #first value is sum of avg losses
    downs = downs.drop(downs.index[:(period-1)])
    rs = ups.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() / \
         downs.ewm(com=period-1,min_periods=0,adjust=False,ignore_na=False).mean() 
    rsi = 100 - 100 / (1 + rs)

    # Calculate StochRSI 
    stochrsi  = (rsi - rsi.rolling(period).min()) / (rsi.rolling(period).max() - rsi.rolling(period).min())
    stochrsi_K = stochrsi.rolling(smoothK).mean()
    stochrsi_D = stochrsi_K.rolling(smoothD).mean()
    return stochrsi, stochrsi_K, stochrsi_D

In [6]:
ratios

[0, 0.236, 0.382, 0.5, 0.618, 0.786, 1, 1.414, 1.618]

In [7]:
ada15 = pd.read_json('BN-main/LINK_USDT-1h.json')
ada15

0        1        2        3        4           5
0      1547632800000   0.5355   0.5355   0.5003   0.5066   63365.330
1      1547636400000   0.5146   0.5162   0.4980   0.4980  153229.700
2      1547640000000   0.4980   0.5021   0.4836   0.4887  185102.780
3      1547643600000   0.4887   0.4973   0.4869   0.4869   67053.330
4      1547647200000   0.4914   0.4920   0.4668   0.4746  168009.300
...              ...      ...      ...      ...      ...         ...
21782  1626235200000  16.1640  16.4180  16.1430  16.3440  138321.838
21783  1626238800000  16.3450  16.3550  16.0820  16.1340  182879.036
21784  1626242400000  16.1340  16.3330  16.0450  16.1370  177371.500
21785  1626246000000  16.1370  16.3560  16.1260  16.3020  190059.879
21786  1626249600000  16.3040  16.3680  16.0470  16.0710  172976.610

[21787 rows x 6 columns]

In [8]:
ada15.columns=['date','open','high','low','close','volume']
ada15

date     open     high      low    close      volume
0      1547632800000   0.5355   0.5355   0.5003   0.5066   63365.330
1      1547636400000   0.5146   0.5162   0.4980   0.4980  153229.700
2      1547640000000   0.4980   0.5021   0.4836   0.4887  185102.780
3      1547643600000   0.4887   0.4973   0.4869   0.4869   67053.330
4      1547647200000   0.4914   0.4920   0.4668   0.4746  168009.300
...              ...      ...      ...      ...      ...         ...
21782  1626235200000  16.1640  16.4180  16.1430  16.3440  138321.838
21783  1626238800000  16.3450  16.3550  16.0820  16.1340  182879.036
21784  1626242400000  16.1340  16.3330  16.0450  16.1370  177371.500
21785  1626246000000  16.1370  16.3560  16.1260  16.3020  190059.879
21786  1626249600000  16.3040  16.3680  16.0470  16.0710  172976.610

[21787 rows x 6 columns]

In [9]:
start = pd.to_datetime('2020-01-01')
ada15.date=pd.to_datetime(ada15['date'],unit='ms')
ada15


date     open     high      low    close      volume
0     2019-01-16 10:00:00   0.5355   0.5355   0.5003   0.5066   63365.330
1     2019-01-16 11:00:00   0.5146   0.5162   0.4980   0.4980  153229.700
2     2019-01-16 12:00:00   0.4980   0.5021   0.4836   0.4887  185102.780
3     2019-01-16 13:00:00   0.4887   0.4973   0.4869   0.4869   67053.330
4     2019-01-16 14:00:00   0.4914   0.4920   0.4668   0.4746  168009.300
...                   ...      ...      ...      ...      ...         ...
21782 2021-07-14 04:00:00  16.1640  16.4180  16.1430  16.3440  138321.838
21783 2021-07-14 05:00:00  16.3450  16.3550  16.0820  16.1340  182879.036
21784 2021-07-14 06:00:00  16.1340  16.3330  16.0450  16.1370  177371.500
21785 2021-07-14 07:00:00  16.1370  16.3560  16.1260  16.3020  190059.879
21786 2021-07-14 08:00:00  16.3040  16.3680  16.0470  16.0710  172976.610

[21787 rows x 6 columns]

In [10]:
start = pd.to_datetime('2021-01-01')
end = pd.to_datetime('2021-05-30')

## adjust the timeperiods fro 15 x 4 or it will be 15min 1 hour and 2 hours 

ada2021 = ada15.loc[(ada15['date']> start)& (ada15['date']< end)].copy()
ada2021['RSI'] = RSI(ada2021['close'])
ada2021['RSI4']=RSI(ada2021['close'],56)
ada2021['RSI8']=RSI(ada2021['close'],112)

ada2021['STRSI'] = STRSIA(ada2021['close'])[0]
ada2021['STRSIK'] = STRSIA(ada2021['close'])[1]
ada2021['STRSID'] = STRSIA(ada2021['close'])[2]
ada2021['ABST1'] = abs(abs(ada2021['STRSIK']) - abs(ada2021['STRSID']))

ada2021['STRSI4'] = STRSIA(ada2021['close'],56,12,12)[0]
ada2021['STRSIK4'] = STRSIA(ada2021['close'],56,12,12)[1]
ada2021['STRSID4'] = STRSIA(ada2021['close'],56,12,12)[2]
ada2021['ABST4'] = abs(abs(ada2021['STRSIK4']) - abs(ada2021['STRSID4']))


ada2021['STRSI8'] = STRSIA(ada2021['close'],112,24,24)[0]
ada2021['STRSIK8'] = STRSIA(ada2021['close'],112,24,24)[1]
ada2021['STRSID8'] = STRSIA(ada2021['close'],112,24,24)[2]
ada2021['ABST8'] = abs(abs(ada2021['STRSIK8']) - abs(ada2021['STRSID8']))




ada2021

date     open     high      low    close      volume  \
17130 2021-01-01 01:00:00  11.2805  11.5778  11.2443  11.4735  399299.040   
17131 2021-01-01 02:00:00  11.4735  11.6200  11.4200  11.5773  235664.040   
17132 2021-01-01 03:00:00  11.5756  11.6008  11.4454  11.5006  156874.010   
17133 2021-01-01 04:00:00  11.5021  11.5498  11.4025  11.4575  181255.920   
17134 2021-01-01 05:00:00  11.4601  11.4783  11.4006  11.4431   98393.100   
...                   ...      ...      ...      ...      ...         ...   
20693 2021-05-29 19:00:00  25.0470  25.1600  24.2500  24.7170  485678.791   
20694 2021-05-29 20:00:00  24.7170  25.0490  24.1200  24.7210  635037.277   
20695 2021-05-29 21:00:00  24.7320  25.2740  24.4510  25.2380  411791.243   
20696 2021-05-29 22:00:00  25.2410  25.3000  24.7360  25.1190  347397.482   
20697 2021-05-29 23:00:00  25.1040  25.7380  24.6920  25.3650  519388.275   

             RSI       RSI4       RSI8     STRSI  ...    STRSID     ABST1  \
17130        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17131        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17132        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17133        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17134        NaN        NaN        NaN       NaN  ...       NaN       NaN   
...          ...        ...        ...       ...  ...       ...       ...   
20693  31.538717  44.204588  46.585624  0.058930  ...  0.203451  0.082231   
20694  31.578069  44.211219  46.588668  0.067297  ...  0.160264  0.069568   
20695  36.646878  45.070398  46.982718  0.549167  ...  0.145683  0.079449   
20696  35.986054  44.908312  46.902354  0.488199  ...  0.228016  0.140205   
20697  38.456656  45.322196  47.091126  0.716141  ...  0.392618  0.191884   

         STRSI4   STRSIK4   STRSID4     ABST4    STRSI8   STRSIK8   STRSID8  \
17130       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17131       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17132       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17133       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17134       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
...         ...       ...       ...       ...       ...       ...       ...   
20693  0.000000  0.028398  0.089255  0.060857  0.079836  0.331257  0.524817   
20694  0.000472  0.023234  0.080124  0.056890  0.080244  0.313702  0.508861   
20695  0.065593  0.022991  0.070818  0.047827  0.133002  0.300953  0.493121   
20696  0.054663  0.023970  0.061632  0.037662  0.122242  0.288982  0.477609   
20697  0.092353  0.026085  0.052783  0.026698  0.147517  0.276795  0.462262   

          ABST8  
17130       NaN  
17131       NaN  
17132       NaN  
17133       NaN  
17134       NaN  
...         ...  
20693  0.193560  
20694  0.195160  
20695  0.192168  
20696  0.188627  
20697  0.185467  

[3568 rows x 21 columns]

In [11]:
#maxlevels = [13,13,13,13,13,13,13]
#maxlevels = np.array(maxlevels)
#maxlevels

In [12]:
#minlevels = [11,11,11,11,11,11,11]
#minlevels = np.array(minlevels)
#minlevels

In [13]:
ada2021

date     open     high      low    close      volume  \
17130 2021-01-01 01:00:00  11.2805  11.5778  11.2443  11.4735  399299.040   
17131 2021-01-01 02:00:00  11.4735  11.6200  11.4200  11.5773  235664.040   
17132 2021-01-01 03:00:00  11.5756  11.6008  11.4454  11.5006  156874.010   
17133 2021-01-01 04:00:00  11.5021  11.5498  11.4025  11.4575  181255.920   
17134 2021-01-01 05:00:00  11.4601  11.4783  11.4006  11.4431   98393.100   
...                   ...      ...      ...      ...      ...         ...   
20693 2021-05-29 19:00:00  25.0470  25.1600  24.2500  24.7170  485678.791   
20694 2021-05-29 20:00:00  24.7170  25.0490  24.1200  24.7210  635037.277   
20695 2021-05-29 21:00:00  24.7320  25.2740  24.4510  25.2380  411791.243   
20696 2021-05-29 22:00:00  25.2410  25.3000  24.7360  25.1190  347397.482   
20697 2021-05-29 23:00:00  25.1040  25.7380  24.6920  25.3650  519388.275   

             RSI       RSI4       RSI8     STRSI  ...    STRSID     ABST1  \
17130        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17131        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17132        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17133        NaN        NaN        NaN       NaN  ...       NaN       NaN   
17134        NaN        NaN        NaN       NaN  ...       NaN       NaN   
...          ...        ...        ...       ...  ...       ...       ...   
20693  31.538717  44.204588  46.585624  0.058930  ...  0.203451  0.082231   
20694  31.578069  44.211219  46.588668  0.067297  ...  0.160264  0.069568   
20695  36.646878  45.070398  46.982718  0.549167  ...  0.145683  0.079449   
20696  35.986054  44.908312  46.902354  0.488199  ...  0.228016  0.140205   
20697  38.456656  45.322196  47.091126  0.716141  ...  0.392618  0.191884   

         STRSI4   STRSIK4   STRSID4     ABST4    STRSI8   STRSIK8   STRSID8  \
17130       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17131       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17132       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17133       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
17134       NaN       NaN       NaN       NaN       NaN       NaN       NaN   
...         ...       ...       ...       ...       ...       ...       ...   
20693  0.000000  0.028398  0.089255  0.060857  0.079836  0.331257  0.524817   
20694  0.000472  0.023234  0.080124  0.056890  0.080244  0.313702  0.508861   
20695  0.065593  0.022991  0.070818  0.047827  0.133002  0.300953  0.493121   
20696  0.054663  0.023970  0.061632  0.037662  0.122242  0.288982  0.477609   
20697  0.092353  0.026085  0.052783  0.026698  0.147517  0.276795  0.462262   

          ABST8  
17130       NaN  
17131       NaN  
17132       NaN  
17133       NaN  
17134       NaN  
...         ...  
20693  0.193560  
20694  0.195160  
20695  0.192168  
20696  0.188627  
20697  0.185467  

[3568 rows x 21 columns]

In [14]:
high = ada2021.high
low = ada2021.low
volume = ada2021.volume
maximums5 = high.rolling(5,5)
max5 = maximums5.max()
minimums5 = low.rolling(5,5)
min5 = minimums5.min()
maximums10 = high.rolling(10,10)
max10 = maximums10.max()
minimums10 = low.rolling(10,10)
min10 = minimums10.min()
volume5 = volume.rolling(5,5)
vmax5 = volume5.max()
volume10 = volume.rolling(10,10)
vmax10 = volume10.max()


In [13]:
len(max5)

3568

In [15]:

ada2021['max5'] = max5
ada2021['max10'] = max10
ada2021['min5'] = min5
ada2021['min10'] = min10
ada2021['vmax5'] = vmax5
ada2021['vmax10'] = vmax10

ada2021.tail()

date    open    high     low   close      volume  \
20693 2021-05-29 19:00:00  25.047  25.160  24.250  24.717  485678.791   
20694 2021-05-29 20:00:00  24.717  25.049  24.120  24.721  635037.277   
20695 2021-05-29 21:00:00  24.732  25.274  24.451  25.238  411791.243   
20696 2021-05-29 22:00:00  25.241  25.300  24.736  25.119  347397.482   
20697 2021-05-29 23:00:00  25.104  25.738  24.692  25.365  519388.275   

             RSI       RSI4       RSI8     STRSI  ...    STRSI8   STRSIK8  \
20693  31.538717  44.204588  46.585624  0.058930  ...  0.079836  0.331257   
20694  31.578069  44.211219  46.588668  0.067297  ...  0.080244  0.313702   
20695  36.646878  45.070398  46.982718  0.549167  ...  0.133002  0.300953   
20696  35.986054  44.908312  46.902354  0.488199  ...  0.122242  0.288982   
20697  38.456656  45.322196  47.091126  0.716141  ...  0.147517  0.276795   

        STRSID8     ABST8    max5   max10   min5  min10       vmax5  \
20693  0.524817  0.193560  26.488  27.647  24.25  24.25  847770.489   
20694  0.508861  0.195160  26.488  27.604  24.12  24.12  847770.489   
20695  0.493121  0.192168  26.297  27.550  24.12  24.12  635037.277   
20696  0.477609  0.188627  25.300  26.847  24.12  24.12  635037.277   
20697  0.462262  0.185467  25.738  26.847  24.12  24.12  635037.277   

           vmax10  
20693  847770.489  
20694  847770.489  
20695  847770.489  
20696  847770.489  
20697  847770.489  

[5 rows x 27 columns]

In [16]:
#maxnew = np.ones_like(ratios)
#maxnew

In [17]:
#addmin = mintest.tolist()
#addmax = maxtest.tolist()
#data = pd.DataFrame({"max":maxtest,"min":mintest},dtype='float')
#data = data.append(addmin,ignore_index=True)
#data1 = pd.DataFrame(maxtest)
#data2 = pd.DataFrame(mintest)
#data = pd.DataFrame(data1,data2)

In [18]:
#datamul = data.mul([2,1],axis='columns')
#datamul = data['max'].mul(ratios[7])

In [19]:
#datamul

In [20]:
#df = ada2021.loc[(ada2021['max10']>0)& (ada2021['min10']>0)]
df = ada2021
#len(df['date'])
average = df['max5']-df['min5']
avg = average.mean()
avg
df
#point = df.loc[(df['max5'].diff()>0)]
#pointm = df.loc[(df['min5'].diff()>0)]

df['support5']= df.min5.rolling(5,5).min()
df['support10']= df.min10.rolling(10,10).min()
df['resist5']= df.max5.rolling(5,5).max()
df['resist10']= df.max10.rolling(10,10).max()

#df['RSI'] = RSI(df['close'])
#df['STRSI4']=STRSIA(df['close'],56,12,12)
#df['STRSI8']=STRSIA(df['close'],112,24,24)


point = df[(df['max5'] > df['max5'].shift(1)) &  (df['max5'].shift(1) > df['max5'].shift(2))]
pointm = df[(df['min5'] < df['min5'].shift(1)) &  (df['min5'].shift(1) > df['min5'].shift(2))]
point
#ada2021
test =df.loc[df['STRSI'] < 0.2]
test

#for row in range(0,len(pointm)):
#    print(pointm['support5'])

date     open     high      low    close      volume  \
17157 2021-01-02 04:00:00  11.7314  11.9420  11.7058  11.7328  295069.130   
17158 2021-01-02 05:00:00  11.7365  11.7529  11.6729  11.7246   95656.790   
17159 2021-01-02 06:00:00  11.7264  11.7517  11.6239  11.6586  162552.590   
17160 2021-01-02 07:00:00  11.6641  11.7198  11.6167  11.6199  106309.870   
17161 2021-01-02 08:00:00  11.6199  11.6480  11.5568  11.5791  163203.080   
...                   ...      ...      ...      ...      ...         ...   
20689 2021-05-29 15:00:00  25.9400  25.9400  25.0380  25.3980  761548.253   
20691 2021-05-29 17:00:00  26.2720  26.2970  24.8330  25.1000  500063.799   
20692 2021-05-29 18:00:00  25.0890  25.2570  24.6220  25.0520  533597.671   
20693 2021-05-29 19:00:00  25.0470  25.1600  24.2500  24.7170  485678.791   
20694 2021-05-29 20:00:00  24.7170  25.0490  24.1200  24.7210  635037.277   

             RSI       RSI4       RSI8     STRSI  ...    max5    max10  \
17157  51.278716        NaN        NaN  0.146389  ...  11.942  12.0941   
17158  50.929362        NaN        NaN  0.135683  ...  11.942  12.0941   
17159  48.089522        NaN        NaN  0.075596  ...  11.942  12.0941   
17160  46.453840        NaN        NaN  0.000000  ...  11.942  12.0284   
17161  44.726618        NaN        NaN  0.000000  ...  11.942  11.9420   
...          ...        ...        ...       ...  ...     ...      ...   
20689  30.694615  44.847246  46.964285  0.000000  ...  27.604  28.9850   
20691  33.222367  44.703187  46.838667  0.158869  ...  26.847  28.2840   
20692  33.015406  44.641070  46.807053  0.145861  ...  26.847  27.6880   
20693  31.538717  44.204588  46.585624  0.058930  ...  26.488  27.6470   
20694  31.578069  44.211219  46.588668  0.067297  ...  26.488  27.6040   

          min5    min10       vmax5      vmax10  support5  support10  resist5  \
17157  11.4303  11.4303  456680.200  456680.200   11.4303    11.3345  12.0941   
17158  11.4303  11.4303  295069.130  456680.200   11.4303    11.4303  12.0941   
17159  11.6239  11.4303  295069.130  456680.200   11.4303    11.4303  12.0284   
17160  11.6167  11.4303  295069.130  456680.200   11.4303    11.4303  11.9420   
17161  11.5568  11.4303  295069.130  456680.200   11.4303    11.4303  11.9420   
...        ...      ...         ...         ...       ...        ...      ...   
20689  25.0380  25.0380  816432.489  816432.489   25.0380    25.0380  28.6740   
20691  24.8330  24.8330  847770.489  847770.489   24.8330    24.8330  27.6880   
20692  24.6220  24.6220  847770.489  847770.489   24.6220    24.6220  27.6470   
20693  24.2500  24.2500  847770.489  847770.489   24.2500    24.2500  27.6040   
20694  24.1200  24.1200  847770.489  847770.489   24.1200    24.1200  27.5500   

       resist10  
17157    12.460  
17158    12.460  
17159    12.460  
17160    12.350  
17161    12.350  
...         ...  
20689    29.734  
20691    29.734  
20692    29.734  
20693    29.734  
20694    29.406  

[991 rows x 31 columns]

In [24]:
import plotly.graph_objs as go
from plotly.subplots import make_subplots


#Declare figure


fig = go.Figure()

fig = make_subplots(rows=9, cols=1,subplot_titles=("Price","gap","empty", "RSI 1 4 8", "Stoch 1", "Stoch 4","Stoch 8","Stoch 1 4 8","Abs Stoch"))
    

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI'],
        name="RSI",
        text="RSI",
        textposition="top center"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI4'],name="RSI4"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['RSI8'],name="RSI8"),
    row=4, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI'],name="STRSI"),
    row=5, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK'],name="STRSIK"),
    row=5, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID'],name="STRSID"),
    row=5, col=1
)
    
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI4'],name="STRSI4"),
    row=6, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK4'],name="STRSIK4"),
    row=6, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID4'],name="STRSID4"),
    row=6, col=1
)
    
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI8'],name="STRSI8"),
    row=7, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSIK8'],name="STRSIK8"),
    row=7, col=1
)

fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSID8'],name="STRSIK8"),
    row=7, col=1
)


fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI8'],name="STRSI8"),
    row=8, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI4'],name="STRSI4"),
    row=8, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['STRSI'],name="STRSI"),
    row=8, col=1
)


fig.add_trace(
    go.Scatter(x=df.date, y=df['ABST1'],name="ABST1"),
    row=9, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['ABST4'],name="ABST4"),
    row=9, col=1
)
fig.add_trace(
    go.Scatter(x=df.date, y=df['ABST8'],name="ABST8"),
    row=9, col=1
)



fig.add_trace(
    go.Scatter(x=df.date, y=df['vmax10'],name="vmax10"),
    row=2, col=1
)
#add Traces

fig.add_trace(go.Candlestick(x=df.date,
                open=df['open'],
                high=df['high'],
                low=df['low'],
                close=df['close'], name = 'market data'),row=1,col=1)

#fig.add_trace(go.Scatter(x=df['date'], y=df['max10']))

#fig.add_trace(go.Scatter(x=df['date'], y=df['min10']))

#fig.add_trace(go.Scatter(x=point['date'], y=point['resist5']))

#fig.add_trace(go.Scatter(x=pointm['date'], y=pointm['support5']))


#fig.add_shape(type="line",
#    x0=pointm['date'], y0=pointm['support5'], x1=max(pointm['date']), y1=pointm['support5'],
#    line=dict(
#        color="LightSeaGreen",
#        width=4,
#        dash="dashdot",
#    ))
fig.update_shapes(dict(xref='x', yref='y'))

#for index in range(0,len(pointm)):
    #fig.add_hline(y=pointm['support5'])

#fig.add_trace(go.Scatter(x=point['date'], y=point['resist10']))

#fig.add_trace(go.Scatter(x=pointm['date'], y=pointm['support10']))
#for i in range(len(df['date'])):
    #fig.add_hline(y=df[i]['min10'], line_dash="dot",
                  #annotation_text="support", 
                  #annotation_position="bottom right")

#fig.add_hline(y=df['max10'], line_dash="dot",
#              annotation_text="resitance", 
#              annotation_position="bottom right")



fig.update_layout(height=3000, width=800, title_text="top sub plots")
# X and Y Axis Update
fig.update_xaxes(
    title = 'Date',rangeslider_visible=False
)

#fig.update_yaxes(
#    title = 'Share Price (USD)'
#)

#Show
fig.show()